In [1]:
"""
Thesis_PhD_Qianqian Predicted_fluxes_glboal_stripes
date: 24-Feb-2023
author: Qianqian
Contact: q.han@utwente.nl
-------------------------------------
Description: 
"""
# libraries
import os
import joblib
from osgeo import gdal
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from pathlib import Path
from rasterio.warp import reproject, Resampling
import xarray as xr
import pickle
from PyStemmusScope import variable_conversion as vc
from rasterio.warp import reproject, Resampling
from sklearn.preprocessing import OneHotEncoder
import time
import os
import re
import argparse
import glob

import sklearn
print(sklearn.__version__)

1.2.2


In [2]:
# load trained RF model
with open('/gpfs/work1/0/einf2480/global_data_Qianqian/RF_train/RFLEH-LAI-hc-CO2-SSM-Vcmo-IGBP_multi7_1core_snellius.pkl', 'rb') as f:
    rfLEHmulti = pickle.load(f)


In [3]:
# load trained RF model
with open('/gpfs/work1/0/einf2480/global_data_Qianqian/RFLEH-LAI-hc-CO2-SSM-Vcmo-IGBP_multi2.pkl', 'rb') as f:
    rfLEHmulti_parallel = pickle.load(f)

/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:318: UserWarning: Trying to unpickle estimator DecisionTreeRegressor from version 1.1.1 when using version 1.2.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:318: UserWarning: Trying to unpickle estimator RandomForestRegressor from version 1.1.1 when using version 1.2.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:318: UserWarning: Trying to unpickle estimator MultiOutputRegressor from version 1.1.1 when using version 1.

In [4]:
def get_directories_with_number_and_ending(directory_path, ending):
    directories = []
    if ending:
        pattern = re.compile(r'^\d+.*{}$'.format(re.escape(ending)))  # Match directory names with number at the beginning and specific ending
    else:
        pattern = re.compile(r'^\d+$')  # Match directory names with only numbers

    for entry in os.scandir(directory_path):
        if entry.is_dir():
            directory_name = entry.name
            if pattern.match(directory_name):
                directories.append(directory_name)

    return directories

In [21]:
def Read_LSFs_Estimated_fluxes(process, job):
    # get all the filefolders named as year
    year_list = get_directories_with_int("/gpfs/work1/0/einf2480/global_data_Qianqian/")
    # the input data from year[0] to year[..], based on the process id in sbatch script
    year = year_list[process-1]
    print(year)
    # reference file for spatial resample
    t = '2011-03-01T00:00:00.000000000'
    era5 = xr.open_dataset('/gpfs/work1/0/einf2480/global_data_Qianqian/era5-land_10m_u_component_of_wind_2011-03_FI-Hyy.nc').sel(time=t, method='nearest')['u10']
    starttime0 = time.time()
    
    ### 0) read era5land data
    a = [file for file in glob.glob("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/era5land/*01*.nc", recursive=True) if '-01' in file]
    all1 = xr.open_mfdataset(a)
    all_resample = all1.resample(time="1800S").interpolate('linear')
    # 累减得到每小时的辐射
    Rin = all1.to_array()[2,:,:,:].copy().astype(float)
    Rin[::] = np.nan
    Rli = all1.to_array()[3,:,:,:].copy().astype(float)
    Rli[::] = np.nan
    for count_i,t in zip(range(745), all1.time.to_numpy()):
        ds_era5land0 = all1.sel(time=np.datetime64(t)- np.timedelta64(1,'h'), method='nearest').compute()
        ds_era5land = all1.sel(time=t, method='nearest').compute()
        ds0 = xr.merge([ds_era5land0])
        ds = xr.merge([ds_era5land])

        ds_ss = xr.Dataset()
        if (pd.to_datetime(t).hour==1):
            # print(t)
            ds_ss["Rin"] = (ds["ssrd"]) / 3600  # J * hr / m2 ->  W / m2
            ds_ss["Rli"] = (ds["strd"]) / 3600  # J * hr / m2 ->  W / m2
        else:
            ds_ss["Rin"] = (ds["ssrd"]-ds0['ssrd']) / 3600  # J * hr / m2 ->  W / m2
            ds_ss["Rli"] = (ds["strd"]-ds0['strd']) / 3600  # J * hr / m2 ->  W / m2
        Rin[count_i,:,:] = ds_ss["Rin"]
        Rli[count_i,:,:] = ds_ss["Rli"]
    #对辐射进行线性插值到半小时
    Rin = Rin.resample(time="1800S").interpolate('linear')
    Rli = Rli.resample(time="1800S").interpolate('linear')
    
    
    ### 1) read LAI data
    probav_files = sorted(Path("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/lai/").glob("*"+year+"01*.nc"))
    print(probav_files)
    lai_10km = []
    for i in probav_files:
        lai0 = xr.open_dataset(i)["LAI"].sel(lat=slice(65, 60), lon=slice(20, 25))
        # print(lai.values)

        lai0 = lai0.rio.write_crs('EPSG:4326')
        era5 = era5.rio.write_crs('EPSG:4326')
        lai0.rio.write_nodata(lai0.rio.nodata, inplace=True)
        #好像不能同时重采样多个波段，不然nan值会互相影响。从python导出的LAI，然后在ArcGIS打开看着一样，但是在python里面，non-nan值的个数却不一样。
        lai0_10km = lai0.rio.reproject_match(era5, resampling=Resampling.average)
        lai0_10km = lai0_10km.assign_coords({
            "x": lai0_10km.x,
            "y": lai0_10km.y,
        })
        lai_10km.append(lai0_10km)
    lai = xr.concat(lai_10km, dim='time').resample(time="1800S").interpolate('linear').rename({'x':'longitude','y':'latitude'})
    
    ### 2) read canopy height data
    hc_path = '/gpfs/work1/0/einf2480/global_data_Qianqian/'+year+'/canopy_height/mosaic_output10km.tif'
    hc = xr.open_dataset(hc_path, engine="rasterio").rename({'x':'longitude','y':'latitude'}).band_data
    
    
    ### 3) read CO2 data
    ds_co2 = xr.open_mfdataset("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/co2/CAMS_CO2_20*.nc")['co2'].sel(time=year).sel(latitude=slice(65, 60), longitude=slice(20, 25))
    ds_co2 = ds_co2.sel(time=ds_co2['time.month'] == 1)
    # convert unit: kg/kg to mg/m3
    ds_co2 = vc.co2_mass_fraction_to_kg_per_m3(ds_co2)*1e6
    # convert the longitude from [0, 360] to [-180, 180]
    lon_name = 'longitude'
    ds_co2['longitude_adjusted'] = xr.where(
        ds_co2[lon_name] > 180,
        ds_co2[lon_name] - 360,
        ds_co2[lon_name])
    ds_co2 = (
        ds_co2
        .swap_dims({lon_name: 'longitude_adjusted'})
        .sel(**{'longitude_adjusted': sorted(ds_co2.longitude_adjusted)})
        .drop(lon_name))
    ds_co2 = ds_co2.rename({'longitude_adjusted': lon_name})
    ds_co2 = ds_co2.rio.write_crs('EPSG:4326')
    era5 = era5.rio.write_crs('EPSG:4326')
    ds_co2.rio.write_nodata(ds_co2.rio.nodata, inplace=True)
    ds_co2_10km = ds_co2.rio.reproject_match(era5, resampling=Resampling.average)
    ds_co2_10km = ds_co2_10km.assign_coords({
        "x": ds_co2_10km.x,
        "y": ds_co2_10km.y,
    })
    ds_co2_10km = ds_co2_10km.resample(time="1800S").interpolate('linear').rename({'x':'longitude','y':'latitude'})
    #CO2有1483个波段，ERA5-Land有1487个波段。一个到21点，一个到23点。
    #值得注意的是ERA5-Land的时间是每个step的结束时间，而CO2是每个step的开始时间？
    #2011-03-01T00:30:00.000000000 在ERA5-Land代表的是00:00-00:30，而在CO2代表00:30-01:00？
    ds_co2_10km=ds_co2_10km.assign_coords({'time':('time',ds_co2_10km.time.values + np.timedelta64(30,'m'),ds_co2_10km.time.attrs)})
    #https://stackoverflow.com/questions/64737439/xarray-dataset-change-value-of-coordinates-while-keeping-attributes
    
    
    ### 4) read SSM data
    path_SSM = glob.glob("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/ssm/SM201*.tif")[0]
    ds_SSM = xr.open_rasterio(path_SSM, engine="rasterio")
    ds_SSM = ds_SSM.sortby(["x", "y"])
    ds_SSM = ds_SSM.sel(x=slice(20,25), y=slice(60, 65))
    ds_SSM['band'] = pd.to_datetime(ds_SSM.band-1, unit='D', origin=str(path_SSM.split('/')[-1][2:6]))
    ds_SSM = ds_SSM.rename({'band':'time'})
    SSM_10km = []
    for i in ds_SSM.time[0:31]:
        SSM0 = ds_SSM.sel(time=i)
        SSM0 = SSM0.rio.write_crs('EPSG:4326')
        era5 = era5.rio.write_crs('EPSG:4326')
        SSM0.rio.write_nodata(SSM0.rio.nodata, inplace=True)
        #好像不能同时重采样多个波段，不然nan值会互相影响。从python导出的LAI，然后在ArcGIS打开看着一样，但是在python里面，non-nan值的个数却不一样。
        SSM0_10km = SSM0.rio.reproject_match(era5, resampling=Resampling.average, nodata=np.nan) #
        SSM0_10km = SSM0_10km.assign_coords({
            "x": SSM0_10km.x,
            "y": SSM0_10km.y,
        })
        SSM_10km.append(SSM0_10km)
    SSM = xr.concat(SSM_10km, dim='time').resample(time="1800S").interpolate('linear').rename({'x':'longitude','y':'latitude'})/1000 
    
    
    ### 5) read Vcmax data
    ds_Vcmo = xr.open_rasterio("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/vcmax/TROPOMI_Vmax_Tg_mean10km.tif", engine="rasterio")
    
    
    ### 6) read IGBP data
    path_landcover = "/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/igbp/landcover10km.tif"
    landcover = xr.open_rasterio(path_landcover, engine="rasterio")
    FILEPATH_LANDCOVER_TABLE = "/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/igbp/lccs_to_igbp_table.csv"
    IGBP_table = pd.read_csv(FILEPATH_LANDCOVER_TABLE)
    IGBP = np.vectorize(IGBP_table.set_index("lccs_class").T.to_dict('records')[0].get)(landcover.values)
    training_testing_append = pd.read_csv('/gpfs/work1/0/einf2480/global_data_Qianqian/training_testing-withindex_v2.csv')
    IGBP_all = pd.DataFrame(columns=['IGBP_veg_long1', 'IGBP_veg_long2', 'IGBP_veg_long3','IGBP_veg_long4','IGBP_veg_long5',
                              'IGBP_veg_long6','IGBP_veg_long7','IGBP_veg_long8','IGBP_veg_long9',
                             'IGBP_veg_long10','IGBP_veg_long11'])
    # define one hot encoding for IGBP
    encoder = OneHotEncoder(categories=[training_testing_append['IGBP_veg_long'].unique()]*1,sparse=False,
                           handle_unknown = "ignore")
    # transform data
    aa = encoder.fit_transform(IGBP.reshape(IGBP.shape[1]*IGBP.shape[1],1))
    # assign 23-D IGBP into 23 columns
    for i in range(1,12,1):
        IGBP_all['IGBP_veg_long'+str(i)] = aa[:,i-1]
    
    
    ### end) combine predictor variables and predict
    result_LE = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_LE[::] = np.nan
    result_H = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_H[::] = np.nan
    #static predictors
    hc_line = hc[0,:,:].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size) #如果和动态变量一样放进ds_ss里显示为一些离散的点，不知道为什么，所以静态变量放在时间循环外面
    Vcmo_line = ds_Vcmo[0,:,:].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP1 = IGBP_all.iloc[:,0].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP2 = IGBP_all.iloc[:,1].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP3 = IGBP_all.iloc[:,2].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP4 = IGBP_all.iloc[:,3].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP5 = IGBP_all.iloc[:,4].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP6 = IGBP_all.iloc[:,5].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP7 = IGBP_all.iloc[:,6].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP8 = IGBP_all.iloc[:,7].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP9 = IGBP_all.iloc[:,8].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP10 = IGBP_all.iloc[:,9].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP11 = IGBP_all.iloc[:,10].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    print('read data{}seconds'.format(time.time() - starttime0))     
    
    starttime = time.time()

    for count_i,t in enumerate(all_resample.time.to_numpy()[96:196]):#zip(range(100), all_resample.time.to_numpy()[500:502]): #
        print(t)
        ds_era5land = all_resample.sel(time=t, method='nearest').compute()
        ds = xr.merge([ds_era5land])
        ds_ss = xr.Dataset()
        ds_ss["Rin"] = Rin.sel(time=t, method='nearest').compute()
        ds_ss["Rli"] = Rli.sel(time=t, method='nearest').compute()
        ds_ss["p"] = ds["sp"]/100   # Pa -> hPa
        ds_ss["Ta"] = ds["t2m"] - 273.15  # K -> degC
        ds_ss["ea"] = vc.calculate_es(ds["d2m"] - 273.15)
        ds_ss["u"] = (ds["u10"] ** 2 + ds["v10"] ** 2) ** 0.5
        ds_ss["Precip_msr"] = ds["tp"]*1000   # mm
        ds_ss['LAI'] = lai.sel(time=t, method='nearest').compute()
        ds_ss['CO2'] = ds_co2_10km.sel(time=t, method='nearest').compute()
        ds_ss['SSM'] = SSM.sel(time=t, method='nearest').compute()

        ds_ss = ds_ss.to_array()
        Rin_line = ds_ss[0,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        Rli_line = ds_ss[1,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        p_line = ds_ss[2,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        Ta_line = ds_ss[3,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        ea_line = ds_ss[4,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        u_line = ds_ss[5,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        Precip_msr_line = ds_ss[6,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        LAI_line = ds_ss[7,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        CO2_line = ds_ss[8,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        SSM_line = ds_ss[9,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)

        features_arr = np.concatenate((Rin_line, Rli_line, p_line, Ta_line,ea_line, u_line, Precip_msr_line,
                                       LAI_line, hc_line, CO2_line, SSM_line, Vcmo_line,
                                       IGBP1, IGBP2, IGBP3,IGBP4,IGBP5,IGBP6,IGBP7,IGBP8,IGBP9,IGBP10,IGBP11))
        features_arr = features_arr.transpose()

        # Nan value.
        df_features = pd.DataFrame(data=features_arr)
        df_features_drop_nan = df_features.dropna()
        invalid_index = sorted(set(df_features.index.to_list()) - set(df_features_drop_nan.index.to_list()))

        # # Convert the nan value as 0 for the calculation
        where_are_NaNs = np.isnan(features_arr)
        features_arr[where_are_NaNs] = 0
        
        estimated_LEH = rfLEHmulti.predict(features_arr)
        estimated_LEH[invalid_index] = np.nan
        LEH_map = estimated_LEH.reshape(ds_ss.latitude.size, ds_ss.longitude.size,2)
        result_LE[count_i, ::] = LEH_map[:,:,0]
        result_H[count_i, ::] = LEH_map[:,:,1]
#         print(np.nanmean(result_LE[count_i,::]))
        
#         import matplotlib.pyplot as plt
    
    
#         fig, axs = plt.subplots(nrows=2, ncols=5, figsize=(15, 6))
#         for ax, i, j in zip(axs.flat,range(11),['Rin', 'Rli', 'p', 'Ta', 'ea', 'u', 'Precip_msr', 'LAI', 'CO2','SSM']):
#             ax.set_title(j)
#             x = ax.imshow(ds_ss[i,::],interpolation='none', cmap='viridis')

#             fig.colorbar(x, ax=ax)
#         plt.show()

#         fig, axs = plt.subplots(nrows=1, ncols=2, figsize=(8, 3))
#         for ax, i, j in zip(axs.flat,range(2),['LE', 'H']):
#             ax.set_title(j)
#             x = ax.imshow(LEH_map[:,:,i], interpolation='nearest', cmap='viridis')
#             fig.colorbar(x, ax=ax)
#         plt.show()

#     # export the result
#     result_LE.rio.write_crs('EPSG:4326').rio.to_raster(
#         '/gpfs/work1/0/einf2480/global_data_Qianqian/output/'+year+'LE.tif',
#         tiled=True,  # GDAL: By default striped TIFF files are created. This option can be used to force creation of tiled TIFF files.
#         windowed=True,  # rioxarray: read & write one window at a time
#     )
#     result_H.rio.write_crs('EPSG:4326').rio.to_raster(
#         tiled=True,  # GDAL: By default striped TIFF files are created. This option can be used to force creation of tiled TIFF files.
#         windowed=True,  # rioxarray: read & write one window at a time
#     )
    
    print('That took {} seconds'.format(time.time() - starttime))     
    return process, job, result_LE, result_H

In [18]:
def Read_LSFs_Estimated_fluxes(process, job):
    # get all the filefolders named as year
    year_list = get_directories_with_number_and_ending("/gpfs/work1/0/einf2480/global_data_Qianqian/", "NL")
    # the input data from year[0] to year[..], based on the process id in sbatch script
    year = year_list[process-1]
    print(year)
    # reference file for spatial resample
    era5 = xr.open_dataset('/gpfs/work1/0/einf2480/global_data_Qianqian/2017NL/era5land/era5-land_10m_u_component_of_wind_2017-01_FI-Hyy.nc')
    era5 = era5.sel(time = era5.time.values[0])['u10']
    starttime0 = time.time()
    
    ### 0) read era5land data
    a = [file for file in glob.glob("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/era5land/*01*.nc", recursive=True)]
    all1 = xr.open_mfdataset(a)
    #all1 = xr.open_mfdataset("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/era5land/*01*.nc")
    all_resample = all1.resample(time="1800S").interpolate('linear')
    
    # ç´¯å‡å¾—åˆ°æ¯å°æ—¶çš„è¾å°„
    Rin = all1.to_array()[2,:,:,:].copy().astype(float)
    Rin[::] = np.nan
    Rli = all1.to_array()[3,:,:,:].copy().astype(float)
    Rli[::] = np.nan
    for count_i,t in zip(range(745), all1.time.to_numpy()):
        ds_era5land0 = all1.sel(time=np.datetime64(t)- np.timedelta64(1,'h'), method='nearest').compute()
        ds_era5land = all1.sel(time=t, method='nearest').compute()
        ds0 = xr.merge([ds_era5land0])
        ds = xr.merge([ds_era5land])

        ds_ss = xr.Dataset()
        if (pd.to_datetime(t).hour==1):
            # print(t)
            ds_ss["Rin"] = (ds["ssrd"]) / 3600  # J * hr / m2 ->  W / m2
            ds_ss["Rli"] = (ds["strd"]) / 3600  # J * hr / m2 ->  W / m2
        else:
            ds_ss["Rin"] = (ds["ssrd"]-ds0['ssrd']) / 3600  # J * hr / m2 ->  W / m2
            ds_ss["Rli"] = (ds["strd"]-ds0['strd']) / 3600  # J * hr / m2 ->  W / m2
        Rin[count_i,:,:] = ds_ss["Rin"]
        Rli[count_i,:,:] = ds_ss["Rli"]
    #å¯¹è¾å°„è¿›è¡Œçº¿æ€§æ’å€¼åˆ°åŠå°æ—¶
    Rin = Rin.resample(time="1800S").interpolate('linear')
    Rli = Rli.resample(time="1800S").interpolate('linear')
    
    
    ### 1) read LAI data
    probav_files = sorted(Path("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/lai/").glob("*"+year[0:-2]+"*.nc"))
    print(probav_files)
    lai_10km = []
    for i in probav_files:
        lai0 = xr.open_dataset(i)["LAI"].sel(lat=slice(55, 50), lon=slice(2, 7))
        # print(lai.values)

        lai0 = lai0.rio.write_crs('EPSG:4326')
        era5 = era5.rio.write_crs('EPSG:4326')
        lai0.rio.write_nodata(lai0.rio.nodata, inplace=True)
        #å¥½åƒä¸èƒ½åŒæ—¶é‡é‡‡æ ·å¤šä¸ªæ³¢æ®µï¼Œä¸ç„¶nanå€¼ä¼šäº’ç›¸å½±å“ã€‚ä»Žpythonå¯¼å‡ºçš„LAIï¼Œç„¶åŽåœ¨ArcGISæ‰“å¼€çœ‹ç€ä¸€æ ·ï¼Œä½†æ˜¯åœ¨pythoné‡Œé¢ï¼Œnon-nanå€¼çš„ä¸ªæ•°å´ä¸ä¸€æ ·ã€‚
        lai0_10km = lai0.rio.reproject_match(era5, resampling=Resampling.average)
        lai0_10km = lai0_10km.assign_coords({
            "x": lai0_10km.x,
            "y": lai0_10km.y,
        })
        lai_10km.append(lai0_10km)
    lai = xr.concat(lai_10km, dim='time').resample(time="1800S").interpolate('linear').rename({'x':'longitude','y':'latitude'})
    
    ### 2) read canopy height data
    hc_path = '/gpfs/work1/0/einf2480/global_data_Qianqian/'+year+'/canopy_height/mosaic_output10km.tif'
    hc = xr.open_dataset(hc_path, engine="rasterio").rename({'x':'longitude','y':'latitude'}).band_data
    
    
    ### 3) read CO2 data
    ds_co2 = xr.open_mfdataset("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/co2/CAMS_CO2_20*.nc")['co2'].sel(time=year[0:-2])#.sel(latitude=slice(65, 60), longitude=slice(20, 25))
#     ds_co2 = ds_co2.sel(time=ds_co2['time.month'] == 1)
    # convert unit: kg/kg to mg/m3
    ds_co2 = vc.co2_mass_fraction_to_kg_per_m3(ds_co2)*1e6
    # convert the longitude from [0, 360] to [-180, 180]
    lon_name = 'longitude'
    ds_co2['longitude_adjusted'] = xr.where(
        ds_co2[lon_name] > 180,
        ds_co2[lon_name] - 360,
        ds_co2[lon_name])
    ds_co2 = (
        ds_co2
        .swap_dims({lon_name: 'longitude_adjusted'})
        .sel(**{'longitude_adjusted': sorted(ds_co2.longitude_adjusted)})
        .drop(lon_name))
    ds_co2 = ds_co2.rename({'longitude_adjusted': lon_name})
    ds_co2 = ds_co2.rio.write_crs('EPSG:4326')
    era5 = era5.rio.write_crs('EPSG:4326')
    ds_co2.rio.write_nodata(ds_co2.rio.nodata, inplace=True)
    ds_co2_10km = ds_co2.rio.reproject_match(era5, resampling=Resampling.average)
    ds_co2_10km = ds_co2_10km.assign_coords({
        "x": ds_co2_10km.x,
        "y": ds_co2_10km.y,
    })
    ds_co2_10km = ds_co2_10km.resample(time="1800S").interpolate('linear').rename({'x':'longitude','y':'latitude'})
    #CO2æœ‰1483ä¸ªæ³¢æ®µï¼ŒERA5-Landæœ‰1487ä¸ªæ³¢æ®µã€‚ä¸€ä¸ªåˆ°21ç‚¹ï¼Œä¸€ä¸ªåˆ°23ç‚¹ã€‚
    #å€¼å¾—æ³¨æ„çš„æ˜¯ERA5-Landçš„æ—¶é—´æ˜¯æ¯ä¸ªstepçš„ç»“æŸæ—¶é—´ï¼Œè€ŒCO2æ˜¯æ¯ä¸ªstepçš„å¼€å§‹æ—¶é—´ï¼Ÿ
    #2011-03-01T00:30:00.000000000 åœ¨ERA5-Landä»£è¡¨çš„æ˜¯00:00-00:30ï¼Œè€Œåœ¨CO2ä»£è¡¨00:30-01:00ï¼Ÿ
    ds_co2_10km=ds_co2_10km.assign_coords({'time':('time',ds_co2_10km.time.values + np.timedelta64(30,'m'),ds_co2_10km.time.attrs)})
    #https://stackoverflow.com/questions/64737439/xarray-dataset-change-value-of-coordinates-while-keeping-attributes
    
    
    ### 4) read SSM data
    path_SSM = glob.glob("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/ssm/SM201*.tif")[0]
    ds_SSM = xr.open_rasterio(path_SSM, engine="rasterio")
    ds_SSM = ds_SSM.sortby(["x", "y"])
    #ds_SSM = ds_SSM.sel(x=slice(20,25), y=slice(60, 65))
    ds_SSM['band'] = pd.to_datetime(ds_SSM.band-1, unit='D', origin=str(path_SSM.split('/')[-1][2:6]))
    ds_SSM = ds_SSM.rename({'band':'time'})
    SSM_10km = []
    for i in ds_SSM.time:
        SSM0 = ds_SSM.sel(time=i)
        SSM0 = SSM0.rio.write_crs('EPSG:4326')
        era5 = era5.rio.write_crs('EPSG:4326')
        SSM0.rio.write_nodata(SSM0.rio.nodata, inplace=True)
        #å¥½åƒä¸èƒ½åŒæ—¶é‡é‡‡æ ·å¤šä¸ªæ³¢æ®µï¼Œä¸ç„¶nanå€¼ä¼šäº’ç›¸å½±å“ã€‚ä»Žpythonå¯¼å‡ºçš„LAIï¼Œç„¶åŽåœ¨ArcGISæ‰“å¼€çœ‹ç€ä¸€æ ·ï¼Œä½†æ˜¯åœ¨pythoné‡Œé¢ï¼Œnon-nanå€¼çš„ä¸ªæ•°å´ä¸ä¸€æ ·ã€‚
        SSM0_10km = SSM0.rio.reproject_match(era5, resampling=Resampling.average, nodata=np.nan) #
        SSM0_10km = SSM0_10km.assign_coords({
            "x": SSM0_10km.x,
            "y": SSM0_10km.y,
        })
        SSM_10km.append(SSM0_10km)
    SSM = xr.concat(SSM_10km, dim='time').resample(time="1800S").interpolate('linear').rename({'x':'longitude','y':'latitude'})/1000 
    
    
    ### 5) read Vcmax data
    ds_Vcmo = xr.open_rasterio("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/vcmax/TROPOMI_Vmax_Tg_mean10km.tif", engine="rasterio")
    
    
    ### 6) read IGBP data
    path_landcover = "/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/igbp/landcover10km.tif"
    landcover = xr.open_rasterio(path_landcover, engine="rasterio")
    FILEPATH_LANDCOVER_TABLE = "/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/igbp/lccs_to_igbp_table.csv"
    IGBP_table = pd.read_csv(FILEPATH_LANDCOVER_TABLE)
    IGBP = np.vectorize(IGBP_table.set_index("lccs_class").T.to_dict('records')[0].get)(landcover.values)
    training_testing_append = pd.read_csv('/gpfs/work1/0/einf2480/global_data_Qianqian/RF_train/training_testing-withindex_v3.csv')
    IGBP_all = pd.DataFrame(columns=['IGBP_veg_long1', 'IGBP_veg_long2', 'IGBP_veg_long3','IGBP_veg_long4','IGBP_veg_long5',
                              'IGBP_veg_long6','IGBP_veg_long7','IGBP_veg_long8','IGBP_veg_long9',
                             'IGBP_veg_long10','IGBP_veg_long11'])
    # define one hot encoding for IGBP
    encoder = OneHotEncoder(categories=[training_testing_append['IGBP_veg_long'].unique()]*1,sparse=False,
                           handle_unknown = "ignore")
    # transform data
    aa = encoder.fit_transform(IGBP.reshape(IGBP.shape[1]*IGBP.shape[1],1))
    # assign 23-D IGBP into 23 columns
    for i in range(1,12,1):
        IGBP_all['IGBP_veg_long'+str(i)] = aa[:,i-1]
    
    
    print('read data{} seconds'.format(time.time() - starttime0))   
    ### end) combine predictor variables and predict
    result_LE = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_LE[::] = np.nan
    result_H = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_H[::] = np.nan
    result_Rn = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_Rn[::] = np.nan
    result_RSSM = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_RSSM[::] = np.nan
    result_SIF685 = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_SIF685[::] = np.nan
    result_SIF740 = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_SIF740[::] = np.nan
    result_Actot = all_resample.to_array()[0,:,:,:].copy().astype(float)
    result_Actot[::] = np.nan
    #static predictors
    hc_line = hc[0,:,:].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size) #å¦‚æžœå’ŒåŠ¨æ€å˜é‡ä¸€æ ·æ”¾è¿›ds_ssé‡Œæ˜¾ç¤ºä¸ºä¸€äº›ç¦»æ•£çš„ç‚¹ï¼Œä¸çŸ¥é“ä¸ºä»€ä¹ˆï¼Œæ‰€ä»¥é™æ€å˜é‡æ”¾åœ¨æ—¶é—´å¾ªçŽ¯å¤–é¢
    Vcmo_line = ds_Vcmo[0,:,:].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP1 = IGBP_all.iloc[:,0].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP2 = IGBP_all.iloc[:,1].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP3 = IGBP_all.iloc[:,2].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP4 = IGBP_all.iloc[:,3].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP5 = IGBP_all.iloc[:,4].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP6 = IGBP_all.iloc[:,5].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP7 = IGBP_all.iloc[:,6].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP8 = IGBP_all.iloc[:,7].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP9 = IGBP_all.iloc[:,8].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP10 = IGBP_all.iloc[:,9].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    IGBP11 = IGBP_all.iloc[:,10].to_numpy().reshape(1, hc.latitude.size*hc.longitude.size)
    
    for count_i,t in enumerate(all_resample.time.to_numpy()[-500:],-500):#zip(range(100), all_resample.time.to_numpy()[500:502]): #
        print(t)
        print(count_i)
        starttime0 = time.time()
        ds_era5land = all_resample.sel(time=t, method='nearest').compute()
        ds = xr.merge([ds_era5land])
        ds_ss = xr.Dataset()
        ds_ss["Rin"] = Rin.sel(time=t, method='nearest').compute()
        ds_ss["Rli"] = Rli.sel(time=t, method='nearest').compute()
        ds_ss["p"] = ds["sp"]/100   # Pa -> hPa
        ds_ss["Ta"] = ds["t2m"] - 273.15  # K -> degC
        ds_ss["ea"] = vc.calculate_es(ds["d2m"] - 273.15)
        ds_ss["u"] = (ds["u10"] ** 2 + ds["v10"] ** 2) ** 0.5
        ds_ss["Precip_msr"] = ds["tp"]*1000   # mm
        ds_ss['LAI'] = lai.sel(time=t, method='nearest').compute()
        ds_ss['CO2'] = ds_co2_10km.sel(time=t, method='nearest').compute()
        ds_ss['SSM'] = SSM.sel(time=t, method='nearest').compute()

        ds_ss = ds_ss.to_array()
        Rin_line = ds_ss[0,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        Rli_line = ds_ss[1,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        p_line = ds_ss[2,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        Ta_line = ds_ss[3,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        ea_line = ds_ss[4,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        u_line = ds_ss[5,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        Precip_msr_line = ds_ss[6,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        LAI_line = ds_ss[7,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        CO2_line = ds_ss[8,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)
        SSM_line = ds_ss[9,:,:].to_numpy().reshape(1, ds_ss.latitude.size*ds_ss.longitude.size)

        features_arr = np.concatenate((Rin_line, Rli_line, p_line, Ta_line,ea_line, u_line, Precip_msr_line,
                                       LAI_line, hc_line, CO2_line, SSM_line, Vcmo_line,
                                       IGBP1, IGBP2, IGBP3,IGBP4,IGBP5,IGBP6,IGBP7,IGBP8,IGBP9,IGBP10,IGBP11))
        features_arr = features_arr.transpose()
        print("features_arr",features_arr)
        print('input data orgainze took {} seconds'.format(time.time() - starttime0))  
        starttime1 = time.time()
        # Nan value.
        df_features = pd.DataFrame(data=features_arr)
        df_features_drop_nan = df_features.dropna()
        invalid_index = sorted(set(df_features.index.to_list()) - set(df_features_drop_nan.index.to_list()))

        # # Convert the nan value as 0 for the calculation
        where_are_NaNs = np.isnan(features_arr)
        features_arr[where_are_NaNs] = 0

        estimated_LEH = rfLEHmulti.predict(features_arr)
        estimated_LEH[invalid_index] = np.nan
        LEH_map = estimated_LEH.reshape(ds_ss.latitude.size, ds_ss.longitude.size,7)
        print('1 timestep took {} seconds'.format(time.time() - starttime1))  
        starttime2 = time.time()
        result_LE[count_i, ::] = LEH_map[:,:,0]
        print("LE values",result_LE[count_i, ::].values)
        print("LE mean", np.nanmean(result_LE[count_i, ::]))
        result_H[count_i, ::] = LEH_map[:,:,1]
        result_Rn[count_i, ::] = LEH_map[:,:,2]
        result_RSSM[count_i, ::] = LEH_map[:,:,3]
        result_SIF685[count_i, ::] = LEH_map[:,:,4]
        result_SIF740[count_i, ::] = LEH_map[:,:,5]
        result_Actot[count_i, ::] = LEH_map[:,:,6]
        print('assign values took {} seconds'.format(time.time() - starttime2)) 
    print("LE values after for loop",result_LE.values)
    print("LE mean after for loop",np.nanmean(result_LE))
    export_to_nc(result_LE, '/gpfs/work1/0/einf2480/global_data_Qianqian/output/'+year+'-LE_0616sneJ.nc')
    print("exportLE")
    export_to_nc(result_H, '/gpfs/work1/0/einf2480/global_data_Qianqian/output/'+year+'-H_0616sneJ.nc')
    print("exportH")
    export_to_nc(result_Rn, '/gpfs/work1/0/einf2480/global_data_Qianqian/output/'+year+'-Rn_0616sneJ.nc')
    print("exportRn")
    export_to_nc(result_RSSM, '/gpfs/work1/0/einf2480/global_data_Qianqian/output/'+year+'-RSSM_0616sneJ.nc')
    print("exportRSSM")
    export_to_nc(result_SIF685, '/gpfs/work1/0/einf2480/global_data_Qianqian/output/'+year+'-SIF685_0616sneJ.nc')
    print("exportSIF685")
    export_to_nc(result_SIF740, '/gpfs/work1/0/einf2480/global_data_Qianqian/output/'+year+'-SIF740_0616sneJ.nc')
    print("exportSIF740")
    export_to_nc(result_Actot, '/gpfs/work1/0/einf2480/global_data_Qianqian/output/'+year+'-Actot_0616sneJ.nc')
    print("exportActot")
    return process, job, result_LE, result_H

In [19]:
def export_to_nc(output_data,output_path):
    print("aa", flush=True)
    # method suggested by Bas, flexible
    from netCDF4 import Dataset
    print("bb", flush=True)

    lat = output_data.latitude.values # the list of latitudes
    print('lat',lat, flush=True)
    lon = output_data.longitude.values #
    print('lon', lon, flush=True)
    data = output_data.values # the soil moisture data
    print("data", data, flush=True)

    
    # Create a new empty netCDF file, in NETCDF3_CLASSIC format (more formats are available)
    nc = Dataset(output_path, mode='w', format='NETCDF3_CLASSIC')
    print("nc",nc, flush=True)

    # Create the dimensions, as required by netCDF
    nc.createDimension('x', size=len(lon)) # instead of x,y you can use lon,lat as dimension names
    nc.createDimension('y', size=len(lat))
    nc.createDimension('time', None)

    # Create the variables, as required by netCDF
    var_x = nc.createVariable('x', 'float64', ('x')) # instead of x,y you can use lon,lat as variable names
    var_y = nc.createVariable('y', 'float64', ('y'))
    var_t = nc.createVariable('time', 'float64', ('time',))

    # Fill the x, y, time variables with values
    var_x[:] = lon
    var_y[:] = lat
    # var_t[:] = variable.time.values
    # var_t.setncattr('units', 'seconds since 1970-01-01 00:00:00') # this is only a description; you can change it
    # var_t.setncattr('calendar', 'standard')

    # the actual data to be stored in the netcdf (soilmoisture?)
    var = nc.createVariable('LE', 'float32', ('time','y','x'))
    var[:] = data # if 'data' does not have the same structure as the one created here (time, y, x) you may need to transpose
    print("var",var, flush=True)
    # write the time as last
    var_t_length = data.shape[0] # the number of timesteps
    seconds_since_epoch = (output_data.time.values.astype('datetime64[s]') - np.datetime64('1970-01-01T00:00:00Z')).astype(int)
    var_t[:] = seconds_since_epoch
    print("vart",var_t, flush=True)
    # var_t[:] = [i*3600 for i in range(var_t_length)] # this is a simple computation; you may have a list of times, or you may want to compute the 'unix' time
    nc.close()

In [8]:
sys.setrecursionlimit(1000)

In [20]:
import sys
import sys
print(sys.version)

recursion_limit = sys.getrecursionlimit()
print(f"The current recursion limit is: {recursion_limit}")

3.9.16 | packaged by conda-forge | (main, Feb  1 2023, 21:39:03) 
[GCC 11.3.0]
The current recursion limit is: 1000


In [14]:
process, job, result_LE, result_H = Read_LSFs_Estimated_fluxes(1, 222)

2019NL
[PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901240000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201902030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201902130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201902210000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201903030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201903130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_

/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/xarray/core/indexing.py:1374: PerformanceWarning: Slicing is producing a large chunk. To accept the large
chunk and silence this warning, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': False}):
    ...     array[indexer]

To avoid creating the large chunks, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': True}):
    ...     array[indexer]
  return self.array[key]
/scratch-local/qiahan.2952725/ipykernel_1249695/7390193.py:104: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_SSM = xr.open_rasterio(path_SSM, engine="rasterio")
/scratch-local/qiahan.2952725/ipykernel_1249695/7390193.py:126: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://co

read data605.6332941055298 seconds
2019-12-21T13:30:00.000000000
-500
features_arr [[         nan          nan          nan ...   0.           0.
    0.        ]
 [         nan          nan          nan ...   0.           0.
    0.        ]
 [         nan          nan          nan ...   0.           0.
    0.        ]
 ...
 [         nan          nan 952.82769531 ...   0.           0.
    0.        ]
 [         nan          nan 958.7084375  ...   0.           0.
    0.        ]
 [         nan          nan 957.90371094 ...   0.           0.
    0.        ]]
input data orgainze took 4.993197917938232 seconds
1 timestep took 0.01691460609436035 seconds
LE (17519, 51, 51)
H (17519, 51, 51)
Rn (17519, 51, 51)
RSSM (17519, 51, 51)
SIF685 (17519, 51, 51)
SIF740 (17519, 51, 51)
Actot (17519, 51, 51)
assign values took 0.007989168167114258 seconds
2019-12-21T14:00:00.000000000
-499


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with f

features_arr [[         nan          nan          nan ...   0.           0.
    0.        ]
 [         nan          nan          nan ...   0.           0.
    0.        ]
 [         nan          nan          nan ...   0.           0.
    0.        ]
 ...
 [         nan          nan 952.6528125  ...   0.           0.
    0.        ]
 [         nan          nan 958.53453125 ...   0.           0.
    0.        ]
 [         nan          nan 957.73390625 ...   0.           0.
    0.        ]]
input data orgainze took 5.038983106613159 seconds
1 timestep took 0.016176462173461914 seconds
LE (17519, 51, 51)
H (17519, 51, 51)
Rn (17519, 51, 51)
RSSM (17519, 51, 51)
SIF685 (17519, 51, 51)
SIF740 (17519, 51, 51)
Actot (17519, 51, 51)
assign values took 0.008051156997680664 seconds
2019-12-21T14:30:00.000000000
-498


...

features_arr [[          nan           nan           nan ...    0.
     0.            0.        ]
 [          nan           nan           nan ...    0.
     0.            0.        ]
 [          nan           nan           nan ...    0.
     0.            0.        ]
 ...
 [          nan           nan  994.07972656 ...    0.
     0.            0.        ]
 [          nan           nan 1000.36890625 ...    0.
     0.            0.        ]
 [          nan           nan  999.56011719 ...    0.
     0.            0.        ]]
input data orgainze took 4.9301323890686035 seconds
1 timestep took 0.015935182571411133 seconds
LE (17519, 51, 51)
H (17519, 51, 51)
Rn (17519, 51, 51)
RSSM (17519, 51, 51)
SIF685 (17519, 51, 51)
SIF740 (17519, 51, 51)
Actot (17519, 51, 51)
assign values took 0.010323762893676758 seconds
2019-12-31T23:00:00.000000000
-1


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with f

features_arr [[          nan           nan           nan ...    0.
     0.            0.        ]
 [          nan           nan           nan ...    0.
     0.            0.        ]
 [          nan           nan           nan ...    0.
     0.            0.        ]
 ...
 [          nan           nan  994.05546875 ...    0.
     0.            0.        ]
 [          nan           nan 1000.33554687 ...    0.
     0.            0.        ]
 [          nan           nan  999.51664063 ...    0.
     0.            0.        ]]
input data orgainze took 4.8199238777160645 seconds
1 timestep took 0.015717029571533203 seconds
LE (17519, 51, 51)
H (17519, 51, 51)
Rn (17519, 51, 51)
RSSM (17519, 51, 51)
SIF685 (17519, 51, 51)
SIF740 (17519, 51, 51)
Actot (17519, 51, 51)
assign values took 0.010344743728637695 seconds
aa
bb
lat [55.  54.9 54.8 54.7 54.6 54.5 54.4 54.3 54.2 54.1 54.  53.9 53.8 53.7
 53.6 53.5 53.4 53.3 53.2 53.1 53.  52.9 52.8 52.7 52.6 52.5 52.4 52.3
 52.2 52.1 52.  51.9 51.8 51.

/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with f

RecursionError: maximum recursion depth exceeded while calling a Python object

In [21]:
process, job, result_LE, result_H = Read_LSFs_Estimated_fluxes(1, 222)

2019NL
[PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901240000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201902030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201902130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201902210000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201903030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201903130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_

/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/xarray/core/indexing.py:1374: PerformanceWarning: Slicing is producing a large chunk. To accept the large
chunk and silence this warning, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': False}):
    ...     array[indexer]

To avoid creating the large chunks, set the option
    >>> with dask.config.set(**{'array.slicing.split_large_chunks': True}):
    ...     array[indexer]
  return self.array[key]
/scratch-local/qiahan.2955035/ipykernel_3393646/762111257.py:104: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_SSM = xr.open_rasterio(path_SSM, engine="rasterio")
/scratch-local/qiahan.2955035/ipykernel_3393646/762111257.py:126: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https:

read data595.444226026535 seconds
2019-12-21T13:30:00.000000000
-500
features_arr [[         nan          nan          nan ...   0.           0.
    0.        ]
 [         nan          nan          nan ...   0.           0.
    0.        ]
 [         nan          nan          nan ...   0.           0.
    0.        ]
 ...
 [         nan          nan 952.82769531 ...   0.           0.
    0.        ]
 [         nan          nan 958.7084375  ...   0.           0.
    0.        ]
 [         nan          nan 957.90371094 ...   0.           0.
    0.        ]]
input data orgainze took 4.473028659820557 seconds
1 timestep took 0.018308401107788086 seconds


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with f

LE values [[nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 ...
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]]


...

LE values [[nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 ...
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]
 [nan nan nan ... nan nan nan]]


/scratch-local/qiahan.2955035/ipykernel_3393646/762111257.py:233: RuntimeWarning: Mean of empty slice
  print("LE mean", np.nanmean(result_LE[count_i, ::]))


LE mean nan
assign values took 45.87628364562988 seconds
2019-12-31T19:30:00.000000000
-8
features_arr [[          nan           nan           nan ...    0.
     0.            0.        ]
 [          nan           nan           nan ...    0.
     0.            0.        ]
 [          nan           nan           nan ...    0.
     0.            0.        ]
 ...
 [          nan           nan  994.47707031 ...    0.
     0.            0.        ]
 [          nan           nan 1000.74695313 ...    0.
     0.            0.        ]
 [          nan           nan  999.93820312 ...    0.
     0.            0.        ]]
input data orgainze took 5.296151638031006 seconds
1 timestep took 0.018482685089111328 seconds


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with f

RecursionError: maximum recursion depth exceeded while calling a Python object

In [22]:
result_LE

NameError: name 'result_LE' is not defined

In [11]:
result_LE.values

NameError: name 'result_LE' is not defined

In [101]:
all_resample.time

<xarray.DataArray 'time' (time: 17519)>
array(['2019-01-01T00:00:00.000000000', '2019-01-01T00:30:00.000000000',
       '2019-01-01T01:00:00.000000000', ..., '2019-12-31T22:00:00.000000000',
       '2019-12-31T22:30:00.000000000', '2019-12-31T23:00:00.000000000'],
      dtype='datetime64[ns]')
Coordinates:
  * time     (time) datetime64[ns] 2019-01-01 ... 2019-12-31T23:00:00
Attributes:
    long_name:  time

In [102]:
for count_i,t in enumerate(all_resample.time.to_numpy()[96:],96):#zip(range(100), all_resample.time.to_numpy()[500:502]): #
    print(count_i)
    print(t)

96
2019-01-03T00:00:00.000000000
97
2019-01-03T00:30:00.000000000
98
2019-01-03T01:00:00.000000000
99
2019-01-03T01:30:00.000000000
100
2019-01-03T02:00:00.000000000
101
2019-01-03T02:30:00.000000000
102
2019-01-03T03:00:00.000000000
103
2019-01-03T03:30:00.000000000
104
2019-01-03T04:00:00.000000000
105
2019-01-03T04:30:00.000000000
106
2019-01-03T05:00:00.000000000
107
2019-01-03T05:30:00.000000000
108
2019-01-03T06:00:00.000000000
109
2019-01-03T06:30:00.000000000
110
2019-01-03T07:00:00.000000000
111
2019-01-03T07:30:00.000000000
112
2019-01-03T08:00:00.000000000
113
2019-01-03T08:30:00.000000000
114
2019-01-03T09:00:00.000000000
115
2019-01-03T09:30:00.000000000
116
2019-01-03T10:00:00.000000000
117
2019-01-03T10:30:00.000000000
118
2019-01-03T11:00:00.000000000
119
2019-01-03T11:30:00.000000000
120
2019-01-03T12:00:00.000000000
121
2019-01-03T12:30:00.000000000
122
2019-01-03T13:00:00.000000000
123
2019-01-03T13:30:00.000000000
124
2019-01-03T14:00:00.000000000
125
2019-01-03T14:

In [17]:
# parallel RF model
process, job, result_LE, result_H = Read_LSFs_Estimated_fluxes(1, 222)

2019NL
[PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901240000_GLOBE_PROBAV_V1.5.1.nc')]


/scratch-local/qiahan.2943544/ipykernel_1462774/3708432959.py:104: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_SSM = xr.open_rasterio(path_SSM, engine="rasterio")
/scratch-local/qiahan.2943544/ipykernel_1462774/3708432959.py:126: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_Vcmo = xr.open_rasterio("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/vcmax/TROPOMI_Vmax_Tg_mean10km.tif", engine="rasterio")
/scratch-local/qiahan.2943544/ipykernel_1462774/3708432959.py:131: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  landcover = xr.open_ra

read data182.69654035568237 seconds
2019-01-03T00:00:00.000000000
input data orgainze took 1.8541927337646484 seconds
1 timestep took 0.009989500045776367 seconds
assign values took 0.0022284984588623047 seconds
82.86537566666668
2019-01-03T00:30:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


input data orgainze took 1.8443305492401123 seconds
1 timestep took 0.009015083312988281 seconds
assign values took 0.0022602081298828125 seconds
82.96621833333333
2019-01-03T01:00:00.000000000


...

/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


input data orgainze took 1.845146656036377 seconds
1 timestep took 0.009237527847290039 seconds
assign values took 0.0023190975189208984 seconds
81.10677988888888
2019-01-04T02:30:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


input data orgainze took 1.8167450428009033 seconds
1 timestep took 0.009002208709716797 seconds
assign values took 0.0022726058959960938 seconds
80.16093944444444
That took 106.52538990974426 seconds


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


In [19]:
#single core RF model
process, job, result_LE, result_H = Read_LSFs_Estimated_fluxes(1, 222)

2019NL
[PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901240000_GLOBE_PROBAV_V1.5.1.nc')]


/scratch-local/qiahan.2943544/ipykernel_1462774/2091924725.py:104: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_SSM = xr.open_rasterio(path_SSM, engine="rasterio")
/scratch-local/qiahan.2943544/ipykernel_1462774/2091924725.py:126: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_Vcmo = xr.open_rasterio("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/vcmax/TROPOMI_Vmax_Tg_mean10km.tif", engine="rasterio")
/scratch-local/qiahan.2943544/ipykernel_1462774/2091924725.py:131: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  landcover = xr.open_ra

read data181.52140641212463 seconds
2019-01-03T00:00:00.000000000
input data orgainze took 1.8253726959228516 seconds
1 timestep took 0.007005929946899414 seconds
assign values took 0.0021789073944091797 seconds
67.72745444444445
2019-01-03T00:30:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


input data orgainze took 1.8251187801361084 seconds
1 timestep took 0.006377458572387695 seconds
assign values took 0.002081155776977539 seconds
67.772212
2019-01-03T01:00:00.000000000


...

/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


input data orgainze took 1.828706979751587 seconds
1 timestep took 0.006302595138549805 seconds
assign values took 0.0021245479583740234 seconds
60.73683298888889
2019-01-04T02:30:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


input data orgainze took 1.8383991718292236 seconds
1 timestep took 0.006469249725341797 seconds
assign values took 0.002132892608642578 seconds
62.53348708888888
That took 106.28263187408447 seconds


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


In [12]:
process, job, result_LE, result_H = Read_LSFs_Estimated_fluxes(1, 222)

2019NL
[PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901240000_GLOBE_PROBAV_V1.5.1.nc')]


/scratch-local/qiahan.2917306/ipykernel_1417248/2797717053.py:104: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_SSM = xr.open_rasterio(path_SSM, engine="rasterio")
/scratch-local/qiahan.2917306/ipykernel_1417248/2797717053.py:126: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_Vcmo = xr.open_rasterio("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/vcmax/TROPOMI_Vmax_Tg_mean10km.tif", engine="rasterio")
/scratch-local/qiahan.2917306/ipykernel_1417248/2797717053.py:131: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  landcover = xr.open_ra

read data145.99349117279053 seconds
2019-01-03T00:00:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


69.55955055555555
2019-01-03T00:30:00.000000000


...

133.665377
2019-01-05T01:00:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


135.11290333333332
2019-01-05T01:30:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


135.21293255555557
That took 206.0935459136963 seconds


In [50]:
result_LE

<xarray.DataArray (time: 1487, latitude: 51, longitude: 51)>
dask.array<setitem, shape=(1487, 51, 51), dtype=float64, chunksize=(1487, 51, 51), chunktype=numpy.ndarray>
Coordinates:
  * longitude  (longitude) float32 2.0 2.1 2.2 2.3 2.4 ... 6.6 6.7 6.8 6.9 7.0
  * latitude   (latitude) float32 55.0 54.9 54.8 54.7 ... 50.3 50.2 50.1 50.0
  * time       (time) datetime64[ns] 2019-01-01 ... 2019-01-31T23:00:00
    variable   <U3 'd2m'
Attributes:
    Conventions:  CF-1.6
    history:      2023-06-08 18:10:52 GMT by grib_to_netcdf-2.25.1: /opt/ecmw...

In [11]:
process, job, result_LE, result_H = Read_LSFs_Estimated_fluxes(1, 222)

2019NL
[PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901030000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901130000_GLOBE_PROBAV_V1.5.1.nc'), PosixPath('/gpfs/work1/0/einf2480/global_data_Qianqian/2019NL/lai/c_gls_LAI_201901240000_GLOBE_PROBAV_V1.5.1.nc')]


/scratch-local/qiahan.2917306/ipykernel_1417248/2797717053.py:104: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_SSM = xr.open_rasterio(path_SSM, engine="rasterio")
/scratch-local/qiahan.2917306/ipykernel_1417248/2797717053.py:126: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  ds_Vcmo = xr.open_rasterio("/gpfs/work1/0/einf2480/global_data_Qianqian/"+year+"/vcmax/TROPOMI_Vmax_Tg_mean10km.tif", engine="rasterio")
/scratch-local/qiahan.2917306/ipykernel_1417248/2797717053.py:131: DeprecationWarning: open_rasterio is Deprecated in favor of rioxarray. For information about transitioning, see: https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html
  landcover = xr.open_ra

read data145.93960976600647 seconds
2019-01-03T00:00:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


69.55955055555555
2019-01-03T00:30:00.000000000


...

133.665377
2019-01-05T01:00:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


135.11290333333332
2019-01-05T01:30:00.000000000


/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
/home/qiahan/.conda/envs/firstEnv/lib/python3.9/site-packages/sklearn/base.py:450: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


135.21293255555557
That took 203.79009103775024 seconds
